# Modeling microtubule catastrophe I

<hr>

In [1]:
# Colab setup ------------------
import os, sys, subprocess
if "google.colab" in sys.modules:
    cmd = "pip install --upgrade iqplot colorcet bebi103 arviz cmdstanpy watermark"
    process = subprocess.Popen(cmd.split(), stdout=subprocess.PIPE, stderr=subprocess.PIPE)
    stdout, stderr = process.communicate()
    import cmdstanpy; cmdstanpy.install_cmdstan()
    data_path = "https://raw.githubusercontent.com/justinbois/learnbayes-livecode/main/"
else:
    data_path = "./"
# ------------------------------

import numpy as np
import pandas as pd

import cmdstanpy
import arviz as az

import bebi103

import iqplot

import bokeh.io
bokeh.io.output_notebook()

Loading BokehJS ...

<hr>

In this webinar, we use data from [Gardner, Zanic, et al., Depolymerizing kinesins Kip3 and MCAK shape cellular microtubule architecture by differential control of catastrophe, *Cell*, **147**, 1092-1103, 2011](https://doi.org/10.1016/j.cell.2011.10.037). The authors investigated the dynamics of **[microtubule](https://en.wikipedia.org/wiki/Microtubule) catastrophe**, the switching of a microtubule from a growing to a shrinking state. In particular, they were interested in the time between the start of growth of a microtubule and the catastrophe event. They monitored microtubules in a single-molecule [TIRF assay](https://en.wikipedia.org/wiki/Total_internal_reflection_fluorescence_microscope) by using tubulin (the monomer that comprises a microtubule) that was labeled with a fluorescent marker.

In the file `gardner_zanic_mt_catastrophe.csv` (which you can download [here](https://raw.githubusercontent.com/justinbois/learnbayes-livecode/main/gardner_zanic_mt_catastrophe.csv), we have observed catastrophe times of microtubules in a set of experiments with 12 µM total tubulin concentration. 

## Generative models for the observed time to catastrophe

In this part of the webinar, we will consider we will models for microtubule catastrophe.

- Model 1: The time to catastrophe is Exponentially distributed.
- Model 2: The time to catastrophe is Gamma distributed.
- Model 3: The time to catastrophe is Weibull distributed.

Note that these descriptions are for the likelihood; we have not specified priors. Before proceeding, we should consider the proposed models in the context of biochemical processes that trigger catastrophe.

* Model 1 says that the microtubule catastrophe times are Exponentially distributed. This means that catastrophe is a Poisson process. I.e., a single Poisson process must arrive to induce catastrophe. In other words, catastrophe is a random, memoryless event. The parameter $\beta$ is the characteristic rate for arrival of the event that triggers catastrophe.
* Model 2 says that the microtubule catastrophe times are Gamma distributed. This means that a series of $\alpha$ Poisson processes must arrive to induce catastrophe. Thus, a series of random, memoryless events must arrive. Importantly, these events have the same rate of occurrence and we can have a non-integer number of events. Perhaps a better model would be to allow for an integer number of events, each with a different rate. Thus, the number of events in this case is an *effective* number of events, as if all events happened at the same rate. For $\alpha = 1$, we recover the Exponential distribution.
* Model 3 accounts for aging. As the parameter $\alpha$ of the Weibull distribution grows, a microtubule is increasingly more likely to undergo catastrophe as time goes on. In the special case of $\alpha = 1$, we again recover the Exponential model.

Our modeling strategy here is to choose a simple model for catastrophe, that a single biochemical event, modeled as a Poisson process, triggers catastrophe. Model 2 and Model 3 are more complex, but have the simple model as a special case. This is in general a good strategy; add complexity to models as needed, with the simpler cases being special cases of limits of the more complex models. This aids identification of sufficient complexity.

## First, EDA!

Prior to diving into the modeling, let's take a quick look at the data. We will load in the data set and then plot the [empirical cumulative distribution function](https://en.wikipedia.org/wiki/Empirical_distribution_function), or ECDF. To make the plot, we will use [iqplot](https://iqplot.github.io), a package I wrote to make plots of data sets with exactly one quantitative variable using Bokeh.

In [2]:
# Read in data and take a look
t = np.loadtxt(os.path.join(data_path, 'gardner_zanic_mt_catastrophe.csv'))

p = iqplot.ecdf(t, q='time to catastrophe (min)')
bokeh.io.show(p)

We can immediately see from the ECDF from the inflection point around four minutes that the Exponential distribution, whose cumulative distribution function is

\begin{align}
F(t\mid\beta) = 1 - \mathrm{e}^{-\beta t}
\end{align}

will not be an appropriate model. Nonetheless, we will still take that as a base case and assess it.

## Model 1: Exponential

To fully specify our models, we need to specify priors for the respective parameters. There is more than one way to parametrize each of the three distributions we are using, and it is easy to get confused. (The Negative Binomial distribution messes me up every time!) When I am doing Bayesian modeling, I stick to the parametrization of distributions that [Stan](https://mc-stan.org/docs/functions-reference/index.html) uses. This keeps me out of trouble, knowing that I can always go to a reference. However, when using [numpy.random](https://numpy.org/doc/stable/reference/random/index.html), [scipy.stats](https://docs.scipy.org/doc/scipy/reference/stats.html), [PyMC](https://www.pymc.io/), [Distributions.jl](https://juliastats.org/Distributions.jl/stable/), [R](https://cran.r-project.org/web/views/Distributions.html), or any other packages or software, the parametrizations may vary. I still want to use those packages (and we will use NumPy momentarily), but I want to keep the parametrizations the consistent.

To help me accomplish that, and also to have a good reference about probability distributions, I built the [Distribution Explorer](https://distribution-explorer.github.io). For each distribution in the explorer, there is a table showing how to use the distribution in Stan, NumPy, and SciPy (Julia, R, and PyMC will soon be added). For example, [here is the table for the Exponential distribution](https://distribution-explorer.github.io/continuous/exponential.html#usage).

For the Exponential distribution, there is a single parameter, the _rate parameter_, $\beta$. In reasoning about a prior, I find it is easier to think in terms of the inverse of $\beta$, a characteristic _time_ for catastrophe, $\tau = 1/\beta$. That is, I find the question, "How long does it take for catastrophe to occur?" easier to think about than "What is the rate of catastrophe?".

Let's address that question, "How long does it take for catastrophe to occur?" to come up with a prior for our rate. For physical parameters like this that must take on positive values, I like to take what I call the "bet the farm" approach. The idea is that I start with a ludicrously short time scale, say one nanosecond. Do I think catastrophe happens in a nanosecond? Surely not. Would I bet the farm? (Bet the farm is a figure of speech that means that you are so certain of something that you would bet everything you have on it.) I would. How about one microsecond? I happen to know that proteins fold (that is, form their structure) on the time scale of milliseconds, which should be much faster than triggering catastrophe. So, yes, I would bet the farm that catastrophe happens on a time scale longer than milliseconds. How about one second? That seems fast to me, but I'm starting to think that is not completely outside the realm of possibility. I would bet that it takes longer than a second for catastrophe, but I wouldn't bet the _farm_. So, $10^0$ seconds is my lower bound.

Now, let's think about an absurdly long time, say a year. Would I bet the farm that it takes less than a year for catastrophe? Absolutely! Less than a month? Yes. Less than a day? Yes, I would, but only because I have some more domain knowledge. I know that microtubule dynamics are important for setting up the mitotic spindle, which is an important process in cell division (mitosis). I know that cell division is faster than a day. How about an hour? I definitely would not bet the farm on an hour. Cell divisions can take that long, so an hour is an upper bound for me. An hour is 3600 seconds, but we are doing rough estimates here, so we will take it to be about $10^3$ seconds. Our data are in units of minutes, so we will take our bounds to be about $10^{-1}$ to about $10^2$ minutes.

Now, how do we code this as a prior. I use a Normal distribution for the base-10 logarithm of the parameter. In this case, the parameter is $\tau$, so, I write

\begin{align}
\log_{10} \tau \sim \text{Norm}(\mu_\tau, \sigma_\tau).
\end{align}

I want most of the probability mass to be between the two bounds, so I set the center of the prior to be at the center of my bet-the-farm estimate and the range between the outer and lower bounds to contain about 95% of the probability mass. Thus,

\begin{align}
&\mu_\tau = (\log_{10} \tau_\mathrm{max} + \log_{10}\tau_\mathrm{min}) / 2,\\[1em]
&4\sigma_\tau = \log_{10} \tau_\mathrm{max} - \log_{10}\tau_\mathrm{min}.
\end{align}

In this case, $\mu_\tau = 1/2$ (corresponding to a catastrophe time of about 3 minutes), and $\sigma_\tau = 3/4$. Thus, we have

\begin{align}
\log_{10} \tau \sim \text{Norm}(\mu_\tau, \sigma_\tau).
\end{align}

We need to convert this to a prior for $\beta$ to complete our model, which is done by a transformation,

\begin{align}
&\tau = 10^{\log_{10}\tau},\\[1em]
&\beta = 1/\tau.
\end{align}

We now have our complete model for the Exponential.

\begin{align}
&\log_{10} \tau \sim \text{Norm}(1/2, 3/4),\\[1em]
&\tau = 10^{\log_{10}\tau},\\[1em]
&\beta = 1/\tau,\\[1em]
&t_i \sim \mathrm{Expon}(\beta)\;\forall i,
\end{align}


where $t_i$ denotes measurement $i$. Note that in our likelihood I have made explicit that I am modeling the measured catastrophe times as independent and identically distributed (i.i.d.).

Note also that I could have instead codified the prior using a LogNormal distribution for $\beta$. This would be equivalent and look like a more compact model. However, I think it is easier to read as I have written it. I find it much easier to think about a logarithm of a parameter being Normally distributed than the parameter being Log-Normally distributed. I am always willing to sacrifice concision for clarity (and being less likely to make mistakes!).

## Model 2: Gamma

For the Gamma model, we need also to specify a prior for the parameter $\alpha$, interpreted as the number of Poisson processes, each with rate $\beta$ that must arrive to trigger catastrophe in addition to a prior for $\beta$. The prior we used for $\beta$ in the Exponential model works here as well. To specify a prior for $\alpha$, we note that a lower bound is one; at lease one Poisson process must arrive to achieve catastrophe, as it is a biochemical process. I am not sure how many Poisson processes need to arrive; it could be a dozen or more. We can use a broad Half-Normal distribution for that. We will choose 

\begin{align}
\alpha \sim \text{HalfNorm}(1, 50),
\end{align}

so that there is probability mass all the way out to 100. So, our Model 2 is

\begin{align}
&\alpha \sim \text{HalfNorm}(1, 50),\\[1em]
&\log_{10} \tau \sim \text{Norm}(1/2, 3/4),\\[1em]
&\tau = 10^{\log_{10}\tau},\\[1em]
&\beta = 1/\tau,\\[1em]
&t_i \sim \mathrm{Gamma}(\alpha, \beta)\;\forall i.
\end{align}

Note that the special case where $\alpha = 1$ gives Model 1, the Exponential likelihood.

## Model 3: Weibull

Finally, we consider a model for aging, where catastrophe becomes more likely as the microtubule ages. There is some physiological basis for this, as the tubulin at the tip of a microtuble is bound to GTP, which gets hydrolyzed into GDP over time, and microtubules with GDP-bound tubulin are more prone to catastrophe.

Using Stan's parametrization, the parameters are $\alpha$ (not related to $\alpha$ from the Gamma distribution) and $\sigma$ (not related to $\sigma$ of the Normal distribution). When $\alpha > 1$, the more likely catastrophe is to occur as time goes by. The parameter $\sigma$ is analogous to $\tau = 1/\beta$. In fact, in the special case where $\alpha = 1$, the Weibull distribution is Exponential with parameter $\beta = 1/\sigma$.

So, we can use the same prior for $\sigma$ as we did for $\tau$ in Models 1 and 2. For the parameter $\alpha$ here, we will again take a very weakly informative prior skewed toward values that are greater than one. To that end, we will use a Gamma distribution whose mode is around 1, but whose mean is a bit rightward. We choose

\begin{align}
\alpha \sim \text{Gamma}(3/2, 1),
\end{align}

such that Model 3 is

\begin{align}
&\alpha \sim \text{Gamma}(3/2, 1),\\[1em]
&\log_{10} \sigma \sim \text{Norm}(1/2, 3/4),\\[1em]
&\sigma = 10^{\log_{10}\sigma},\\[1em]
&t_i \sim \mathrm{Weibull}(\alpha, \sigma)\;\forall i.
\end{align}

## Prior predictive checks

It is always wise to check your priors to see if they generate data sets that are almost all within the realm of plausibility and also have good coverage of the realm of possibility. Because these models are fairly simple to work with, we can do prior predictive checks on all of them at once. We could use Stan to do these, but it is easier to just use NumPy.

In [3]:
n_ppc = 50
rng = np.random.default_rng(seed=3252)

# Prior for parameters
alpha_2 = 1 + np.abs(rng.normal(0, 50, size=n_ppc))
alpha_3 = rng.gamma(1.5, 1, size=n_ppc)
log_tau = rng.normal(0.5, 0.75, size=n_ppc)

# Transformations
beta = 1 / 10 ** log_tau
sigma = 10 ** log_tau


t_exp_ppc = [rng.exponential(1 / b, size=len(t)) for b in beta]
t_gamma_ppc = [rng.gamma(a, 1 / b, size=len(t)) for a, b in zip(alpha_2, beta)]
t_weibull_ppc = [rng.weibull(a, size=len(t)) * s for a, s in zip(alpha_3, sigma)]

With our PPC samples drawn, let's make ECDFs of them.

In [4]:
plots = [
    iqplot.ecdf(
        pd.DataFrame(t_ppc).transpose().melt(var_name="trial"),
        q="value",
        cats="trial",
        style="staircase",
        line_kwargs=dict(line_color="#1f78b4", line_width=0.5),
        show_legend=False,
        title=name,
        x_axis_type="log",
        x_axis_label="time to catastrophe (min)",
        frame_height=150,
        x_range=[1e-3, 1e4],
    )
    for name, t_ppc in zip(
        ["exp", "gamma", "weibull"],
        [t_exp_ppc, t_gamma_ppc, t_weibull_ppc],
    )
]

# Lock x-axes
for i in range(1, len(plots)):
    plots[i].x_range = plots[0].x_range

bokeh.io.show(bokeh.layouts.gridplot(plots, ncols=1))

The ECDFs cover what we would expect, the Weibull and Gamma models allow for some extremely long and short times. All models seem to encompass reasonable results based on prior predictive checks. The Gamma model tends to give longer times to catastrophe than the Exponential model, but that is to be expected, since they have the same prior on the rate. Both models still over the realm of possibility for times to catastrophe, so I am satisfied with the prior predictive check.

## Sampling the posteriors

Now, we'll code up the Stan models to do the sampling. Here are the respective Stan models. We save them as Python strings so we can create Stan files from them for compilation both using Colab and locally. Normally, they would be stored in separate, pre-made Stan files.

### Model 1: Exponential

In [5]:
models = {}
models["exp"] = """
data {
  int N;
  array[N] real t;
}


parameters {
  // Log of tau in units of minutes
  real log_tau;
}



transformed parameters {
  real<lower=0> tau = 10 ^ log_tau;
  real<lower=0> beta_ = 1.0 / tau;
}


model {
  log_tau ~ normal(0.5, 0.75);
  
  t ~ exponential(beta_);
}


generated quantities {
  array[N] real t_ppc;

  for (i in 1:N) {
    t_ppc[i] = exponential_rng(beta_);
  }
}
"""

### Model 2: Gamma

In [6]:
models["gamma"] = """
data {
  int N;
  array[N] real t;
}


parameters {
  real<lower=1> alpha;
  real log_tau;
}


transformed parameters {
  real<lower=0> tau = 10 ^ log_tau;
  real<lower=0> beta_ = 1.0 / tau;
}


model {
  alpha ~ normal(1, 50);
  log_tau ~ normal(0.5, 0.75);
  
  t ~ gamma(alpha, beta_);
}


generated quantities {
  array[N] real t_ppc;

  for (i in 1:N) {
    t_ppc[i] = gamma_rng(alpha, beta_);
  }
}
"""

### Weibull

In [7]:
models["weibull"] = """
data {
  int N;
  array[N] real t;
}


parameters {
  real<lower=0> alpha;
  real log_sigma;
}


transformed parameters {
  real<lower=0> sigma = 10 ^ log_sigma;
}


model {
  alpha ~ normal(1.5, 1.0);
  log_sigma ~ normal(0.5, 0.75);
  
  t ~ weibull(alpha, sigma);
}


generated quantities {
  array[N] real t_ppc;

  for (i in 1:N) {
    t_ppc[i] = weibull_rng(alpha, sigma);
  }
}
"""

We can compile each of these models and obtain our samples.

In [8]:
data = dict(t=t, N=len(t))

samples = {}
for model in ["exp", "gamma", "weibull"]:
    fname = f"{model}.stan"
    with open(fname, "w") as f:
        f.write(models[model])

    with bebi103.stan.disable_logging():
        sm = cmdstanpy.CmdStanModel(stan_file=fname)
        samples[model] = az.from_cmdstanpy(
            sm.sample(data=data), posterior_predictive="t_ppc"
        )

chain 1 |          | 00:00 Status

chain 2 |          | 00:00 Status

chain 3 |          | 00:00 Status

chain 4 |          | 00:00 Status

chain 1 |          | 00:00 Status

...

chain 4 |          | 00:00 Status

chain 1 |          | 00:00 Status

chain 2 |          | 00:00 Status

chain 3 |          | 00:00 Status

chain 4 |          | 00:00 Status

### Sampler diagnostics

It's always a good idea to check diagnostics of the sampler.

In [9]:
for model, samps in samples.items():
    print(("\n\n" if model != "exp" else "") + f"Diagnostics for {model}...")
    bebi103.stan.check_all_diagnostics(samps)

Diagnostics for exp...
Effective sample size looks reasonable for all parameters.

Rhat looks reasonable for all parameters.

0 of 4000 (0.0%) iterations ended with a divergence.

0 of 4000 (0.0%) iterations saturated the maximum tree depth of 10.

E-BFMI indicated no pathological behavior.


Diagnostics for gamma...
Effective sample size looks reasonable for all parameters.

Rhat looks reasonable for all parameters.

0 of 4000 (0.0%) iterations ended with a divergence.

0 of 4000 (0.0%) iterations saturated the maximum tree depth of 10.

E-BFMI indicated no pathological behavior.


Diagnostics for weibull...
Effective sample size looks reasonable for all parameters.

Rhat looks reasonable for all parameters.

0 of 4000 (0.0%) iterations ended with a divergence.

0 of 4000 (0.0%) iterations saturated the maximum tree depth of 10.

E-BFMI indicated no pathological behavior.


### Posterior predictive checks

This all looks good! Samples in hand, we can do posterior predictive checks to assess how well the models could generate the observed data set. When I do posterior predictive checks of this sort, I plot envelopes containing percentiles of the ECDFs generated from the model with parameters sampled out of the posterior. I then overlay the ECDF of the observed data.

#### Model 1: Exponential

In [10]:
# Reshape the samples to make predictive ECDF plot
t_ppc = (
    samples["exp"].posterior_predictive["t_ppc"]
    .stack({"sample": ("chain", "draw")})
    .transpose("sample", "t_ppc_dim_0")
)

bokeh.io.show(
    bebi103.viz.predictive_ecdf(
        t_ppc,
        data=t,
        title="Model 1: Exponential",
        x_axis_label='time to catastrophe (min)',
    )
)

The dark blue line is the median of the samples, with the pale blue envelop containing 68% percent of the sampled ECDFs and the very pale blue envelope containing 95% of the sampled ECDFs.

This plot is easier to see if we look at the *difference* of ECDFs. That is, we plot the median sampled ECDF as a straight blue line at zero and the envelopes and observed ECDFs as differences from the median.

In [11]:
bokeh.io.show(
    bebi103.viz.predictive_ecdf(
        t_ppc,
        data=t,
        title="Model 1: Exponential",
        diff="ecdf",
        x_axis_label="time to catastrophe (min)",
    )
)

It is clear here that Model 1, the Exponential model, fails, terribly. The model simply cannot generate the observed data.

#### Model 2: Gamma

Now, let's check out Model 2 (Gamma).

In [12]:
t_ppc = (
    samples['gamma'].posterior_predictive["t_ppc"]
    .stack({"sample": ("chain", "draw")})
    .transpose("sample", "t_ppc_dim_0")
)

bokeh.io.show(
    bebi103.viz.predictive_ecdf(
        t_ppc,
        data=t,
        title="Model 2: Gamma",
        diff='ecdf',
        x_axis_label='time to catastrophe (min)',
    )
)

This looks much better. Just a few, maybe 5%, escape the middle 95 percentile envelope, which is what we would expect. 

#### Model 3: Weibull

Let's see if we get a different result with Weibull.

In [13]:
t_ppc = (
    samples['weibull'].posterior_predictive["t_ppc"]
    .stack({"sample": ("chain", "draw")})
    .transpose("sample", "t_ppc_dim_0")
)

bokeh.io.show(
    bebi103.viz.predictive_ecdf(
        t_ppc,
        data=t,
        title="Model 3: Weibull",
        diff="ecdf",
        x_axis_label="time to catastrophe (min)",
    )
)

The Weibull model performs more poorly in the posterior predictive checks. At this point, we can safely say that the Gamma model is the best of the three, and further that it reasonably captures the data.

## Conclusions

This implies that microtubule catastrophe is not the result of a single Poisson process. Microtubules also do not age in the Weibull sense, which is to say that catastrophe-triggering events do not grow more likely with age. Rather, the observations are commensurate with a series of Poisson processes arriving to trigger catastrophe. We can look at the parameter $\alpha$ to assess how many. We will do this by making a corner plot.

In [14]:
bokeh.io.show(
    bebi103.viz.corner(
        samples["gamma"],
        parameters=[("alpha", "α"), ("tau", "τ (min)")],
        xtick_label_orientation=np.pi / 4,
    )
)

We can interpret this to mean that there are about three Poisson processes that have to arrive in succession to trigger catastrophe. Note that this model assumes that all of the processes arrive at the same rate. From our sampling, that rate is such that the Poisson processes arrive a bit more than two minutes apart on average.

## Really?

Do we really believe this? We'll investigate in the next couple notebooks!

## Computing enviroment

In [15]:
%load_ext watermark
%watermark -v -p numpy,pandas,bebi103,cmdstanpy,arviz,bokeh,jupyterlab
print("cmdstan   :", bebi103.stan.cmdstan_version())

Python implementation: CPython
Python version       : 3.11.4
IPython version      : 8.12.0

numpy     : 1.24.3
pandas    : 1.5.3
bebi103   : 0.1.14
cmdstanpy : 1.1.0
arviz     : 0.16.1
bokeh     : 3.2.1
jupyterlab: 4.0.3

cmdstan   : 2.32.2
